In [64]:
#importing libraries
import numpy as np
np.set_printoptions(suppress=True)
import pandas as pd
pd.set_option('display.max_columns', None)

import math
import warnings
warnings.filterwarnings('ignore')
import pdb

#importing auto encoder code
from autoencoder import AutoEncoder

In [86]:
def one_hot_encoding(dataframe, features=[]):

    for feature in features:
        temp_dataframe = pd.get_dummies(dataframe[feature], prefix=feature)
        dataframe = pd.concat([dataframe, temp_dataframe], axis=1)
        dataframe_dash = dataframe
        
    dataframe = dataframe.drop(columns=features)

    return dataframe


def one_hot_decoding(original_dataframe_features=None, encoded_dataframe=None):
    encoded_list = list(encoded_dataframe)
    
    encoded_feature_list = [x.split('_')[-1] for x in encoded_list]
    encoded_feature_list = np.array(encoded_feature_list)#, dtype='float')
    
    output = encoded_dataframe.values.astype(float)
    output = np.multiply(output, encoded_feature_list)
    
    decode_df = pd.DataFrame(output, columns=encoded_list)

    for feature in original_dataframe_features:
        l = [x for x in encoded_list if feature in x]
        decode_df[feature] = decode_df[l].max(axis=1)

    return decode_df.drop(columns=encoded_list)


def error(y, y_pred):
    return np.mean(np.subtract(y_pred, y)**2)


def test_train_split(dataframe, split_ratio=0.8):
    split_index = int(dataframe.shape[0]*split_ratio)
    train = dataframe.iloc[0:split_index]
    test = dataframe.iloc[split_index:]
    return train, test

In [66]:
def run(train=None, test=None, learning_rate=0.1, corruption_level=0.3, training_epochs=25):
    rng = np.random.RandomState(123)
    
    data = np.nan_to_num(train.values.astype(float))
    # construct dA
    encoder = AutoEncoder(input=data, n_visible=data.shape[1], n_hidden=5, rng=rng)

    print('Training Auto Encoders:\n')
    # train
    for epoch in range(training_epochs):
        encoder.train(lr=learning_rate, corruption_level=corruption_level)
        cost = encoder.mse(corruption_level=corruption_level)
        if epoch % 5 == 0:
            print('Training epoch %d, cost is ' % epoch, cost)
        learning_rate *= 0.95

    
    print('\n\nPrediction on test data: \n')
    #t = np.nan_to_num(test.values.astype(float))
    t_pred = encoder.predict(np.nan_to_num(train.values.astype(float)))
    #print(t)
    #print(t_pred)
    print('error: ',error(data, t_pred))
    return pd.DataFrame(t_pred, columns=list(train))

In [4]:
df = pd.read_csv('ml3_updated_removed_missing_greater_than_50.csv', encoding = 'ISO-8859-1')

In [5]:
print(df.shape)
df[5:7]

(2979, 206)


Site Participant_ID  RowNumber  session_id   age  backcount1  \
5  AshlandUniversity             15        180   7392153.0  18.0       357.0   
6  AshlandUniversity             16        185   7392233.0  18.0       357.0   

   backcount10  backcount2  backcount3  backcount4  backcount5  backcount6  \
5        330.0       354.0       351.0       348.0       345.0       342.0   
6        330.0       354.0       351.0       348.0       345.0       342.0   

   backcount7  backcount8  backcount9  big5_01  big5_02  big5_03  big5_04  \
5       339.0       336.0       333.0      7.0      4.0      5.0      5.0   
6       339.0       336.0       333.0      5.0      5.0      7.0      3.0   

   big5_05  big5_06  big5_07  big5_08  big5_09  big5_10  elm_01  elm_02  \
5      5.0      1.0      7.0      3.0      5.0      2.0     5.0     6.0   
6      6.0      5.0      7.0      2.0      5.0      3.0     5.0     3.0   

   elm_03  elm_04  elm_05 ethnicity gender  intrinsic_01  intrinsic_02  \
5     5.0     5.0     5.0         6      1           2.0           1.0   
6     6.0     3.0     4.0         6      1           3.0           3.0   

   intrinsic_03  intrinsic_04  intrinsic_05  intrinsic_06  intrinsic_07  \
5           1.0           2.0           1.0           2.0           3.0   
6           2.0           3.0           4.0           2.0           2.0   

   intrinsic_08  intrinsic_09  intrinsic_10  intrinsic_11  intrinsic_12  \
5           3.0           2.0           3.0           2.0           2.0   
6           4.0           2.0           3.0           2.0           1.0   

   intrinsic_13  intrinsic_14  intrinsic_15  kposition kratio  lposition  \
5           3.0           3.0           3.0        2.0      3        2.0   
6           2.0           2.0           3.0        1.0      3        2.0   

  lratio       major  mcdv1  mcdv2  mcfiller1  mcfiller2  mcfiller3  mood_01  \
5      7     nursing    0.0    3.0        1.0        0.0        1.0      3.0   
6     35  Psychology    0.0    2.0        2.0        1.0        1.0      2.0   

   mood_02  nfc_01  nfc_02  nfc_03  nfc_04  nfc_05  nfc_06  nposition nratio  \
5      2.0     4.0     4.0     4.0     1.0     1.0     1.0        2.0      4   
6      2.0     2.0     2.0     2.0     3.0     4.0     2.0        2.0     20   

   pate_01  pate_02  pate_03  pate_04  pate_05  rposition rratio  sarcasm  \
5      4.0      3.0      1.0      1.0      2.0        1.0      3      3.0   
6      5.0      5.0      1.0      1.0      2.0        2.0     40      6.0   

   selfesteem_01  stress_01  stress_02  stress_03  stress_04 tempest1  \
5            2.0        5.0        2.0        2.0        4.0       70   
6            5.0        3.0        4.0        4.0        2.0       70   

   tempest2  tempest3  tempfollowup1  tempfollowup2  tempfollowup3  vposition  \
5       4.0       2.0            6.0            6.0            5.0        2.0   
6       6.0       2.0            7.0            7.0            7.0        2.0   

  vratio year Station    Date.x Experimenter  Temperatureinlab OrderofTasks  \
5      5    1       1  9/2/2014          ERS              73.0        SR-II   
6     30    1       1  9/2/2014          ERS              73.0        SR-II   

   ClipboardWeight IIResponse SRCondition SRMeetingResponse  \
5             10.0          7           B            Friday   
6             20.0          7           B            Monday   

  SRConfidenceResponse StartDate.x     EndDate  NumberofDays  Pool2a  Pool2b  \
5                    4   8/25/2014  11/25/2014            92       1       0   
6                    4   8/25/2014  11/25/2014            92       1       0   

   Pool2c  Pool2d  Pool3  Pool4  Pool5a  Pool6  Pool7b  Pool7c  Pool7d  Pool8  \
5       0       0    3.0   0.25     0.0      0       0       0       0      1   
6       0       0    3.0   0.25     0.0      0       0       0       0      1   

   Pool9  Pool10  Pool11  Pool12  Pool13  Pool14  Pool15  Pool16a  Pool16b  \
5    1.0 

In [91]:
df['Site'].value_counts(dropna=False)

MichiganStateUniversity            330
UCRiverside                        262
UniversityOfVirginia               198
TexasAandM                         190
OSUNewark                          157
PennStateAbington                  156
SanDiegoStateUniversity            146
NovaSoutheasternUniversity         146
UniversityOfFlorida                146
MontanaStateUniversity             142
IthacaCollege                      139
UCDavis                            139
BradleyUniversity                  130
PacificLutheranUniversity          113
MiamiUniversity                    105
VirginiaCommonwealthUniversity     104
UniversityOfToronto                 98
UniversityOfSouthernMississippi     96
AshlandUniversity                   96
CarletonUniversity                  50
NaN                                 36
Name: Site, dtype: int64

In [37]:
df_backcount = df.loc[:, 'backcount1':'backcount9']
#df_backcount['backcount10'].value_counts(dropna=False)
#df = df.drop(df[df['backcount6'] == '339`'].index)
df_backcount_encoded = one_hot_encoding(df_backcount, features=list(df_backcount))
df_backcount_encoded.head()
#data = train.values.astype(float)

backcount1_0.0  backcount1_1.0  backcount1_3.0  backcount1_9.0  \
0               0               0               0               0   
1               0               0               0               0   
2               0               0               0               0   
3               0               0               0               0   
4               0               0               0               0   

   backcount1_12.0  backcount1_60.0  backcount1_63.0  backcount1_77.0  \
0                0                0                0                0   
1                0                0                0                0   
2                0                0                0                0   
3                0                0                0                0   
4                0                0                0                0   

   backcount1_120.0  backcount1_157.0  backcount1_257.0  backcount1_277.0  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   
3                 0                 0                 0                 0   
4                 0                 0                 0                 0   

   backcount1_297.0  backcount1_306.0  backcount1_320.0  backcount1_327.0  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   
3                 0                 0                 0                 0   
4                 0                 0                 0                 0   

   backcount1_330.0  backcount1_339.0  backcount1_345.0  backcount1_347.0  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   
3                 0                 0                 0                 0   
4                 0                 0                 0                 0   

   backcount1_351.0  backcount1_356.0  backcount1_357.0  backcount1_358.0  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 1                 0   
3                 0                 0                 1                 0   
4                 0                 0                 1                 0   

   backcount1_359.0  backcount1_360.0  backcount1_363.0  backcount1_367.0  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   
3                 0                 0                 0                 0   
4                 0                 0                 0                 0   

   backcount1_377.0  backcount1_390.0  backcount1_557.0  backcount1_630.0  \
0                 0                 0                 0                 0   
1                 0                 0                 0                 0   
2                 0                 0                 0                 0   
3                 0                 0                 0                 0   
4                 0                 0                 0                 0   

   backcount1_657.0  backcount1_4536.0  backcount1_357357.0  \
0                 0                  0                    0   
1                 0                  0                    0   
2                 0                  0                    0   
3                 0                  0                    0   
4                 0                  0                  

In [46]:
#train, test = test_train_split(df_backcount_encoded.sample(frac=1))
pred_df_backcount = run(train=df_backcount_encoded, training_epochs=100)

Training Auto Encoders:

Training epoch 0, cost is  0.037383749289433624
Training epoch 5, cost is  0.020639094455446677
Training epoch 10, cost is  0.01935620999949367
Training epoch 15, cost is  0.02058098315359425
Training epoch 20, cost is  0.02048219509810802
Training epoch 25, cost is  0.019423076543030434
Training epoch 30, cost is  0.018778741500605673
Training epoch 35, cost is  0.018662029416139644
Training epoch 40, cost is  0.018621360507890188
Training epoch 45, cost is  0.019119489599513005
Training epoch 50, cost is  0.01822936487744824
Training epoch 55, cost is  0.017953939162708175
Training epoch 60, cost is  0.018525336964695792
Training epoch 65, cost is  0.018027663535528
Training epoch 70, cost is  0.018565015010746717
Training epoch 75, cost is  0.018618756364764667
Training epoch 80, cost is  0.018028905640876017
Training epoch 85, cost is  0.018458007244765807
Training epoch 90, cost is  0.017773486273240477
Training epoch 95, cost is  0.017850322276227532


Pr

In [74]:
decoded = one_hot_decoding(list(df_backcount), encoded_dataframe=pred_df_backcount)
decoded.head()
#decoded['backcount1'].value_counts(dropna=False)
#decoded.shape

backcount1  backcount10  backcount2  backcount3  backcount4  backcount5  \
0       330.0        330.0        -0.0        -0.0        -0.0       345.0   
1       330.0        330.0        -0.0        -0.0        -0.0       345.0   
2       357.0        330.0       354.0       351.0       348.0       345.0   
3       357.0        330.0       354.0       351.0       348.0       345.0   
4         0.0         -0.0        -0.0        -0.0        -0.0        -0.0   

   backcount6  backcount7  backcount8  backcount9  
0        -0.0       339.0       336.0        -0.0  
1        -0.0       339.0       336.0        -0.0  
2       342.0       339.0       336.0       333.0  
3       342.0       339.0       336.0       333.0  
4        -0.0        -0.0        -0.0        -0.0

In [80]:
df_backcount.head()
nan_mask = (df_backcount.notnull()).astype('int')

In [81]:
pred = np.multiply(decoded.values, nan_mask)
orig = np.nan_to_num(df_backcount.values)
error(y=orig, y_pred=pred)

backcount1     2.961027e+165
backcount10     3.656603e+07
backcount2      4.256690e+09
backcount3      8.209754e+07
backcount4      4.066041e+07
backcount5      3.995468e+19
backcount6      4.054464e+09
backcount7      3.857704e+19
backcount8      3.804852e+09
backcount9      3.729076e+09
dtype: float64

In [82]:
error(y=df_backcount, y_pred=decoded)

backcount1     3.660124e+165
backcount10     4.525558e+07
backcount2      5.207671e+09
backcount3      1.005214e+08
backcount4      4.988771e+07
backcount5      4.902183e+19
backcount6      4.976616e+09
backcount7      4.739010e+19
backcount8      4.677943e+09
backcount9      4.588566e+09
dtype: float64

In [83]:
df_full = one_hot_encoding(df, features=list(df))
df_full.head()

Site_AshlandUniversity  Site_BradleyUniversity  Site_CarletonUniversity  \
0                       1                       0                        0   
1                       1                       0                        0   
2                       1                       0                        0   
3                       1                       0                        0   
4                       1                       0                        0   

   Site_IthacaCollege  Site_MiamiUniversity  Site_MichiganStateUniversity  \
0                   0                     0                             0   
1                   0                     0                             0   
2                   0                     0                             0   
3                   0                     0                             0   
4                   0                     0                             0   

   Site_MontanaStateUniversity  Site_NovaSoutheasternUniversity  \
0                            0                                0   
1                            0                                0   
2                            0                                0   
3                            0                                0   
4                            0                                0   

   Site_OSUNewark  Site_PacificLutheranUniversity  Site_PennStateAbington  \
0               0                               0                       0   
1               0                               0                       0   
2               0                               0                       0   
3               0                               0                       0   
4               0                               0                       0   

   Site_SanDiegoStateUniversity  Site_TexasAandM  Site_UCDavis  \
0                             0                0             0   
1                             0                0             0   
2                             0                0             0   
3                             0                0             0   
4                             0                0             0   

   Site_UCRiverside  Site_UniversityOfFlorida  \
0                 0                         0   
1                 0                         0   
2                 0                         0   
3                 0                         0   
4                 0                         0   

   Site_UniversityOfSouthernMississippi  Site_UniversityOfToronto  \
0                                     0                         0   
1                                     0                         0   
2                                     0                         0   
3                                     0                         0   
4                                     0                         0   

   Site_UniversityOfVirginia  Site_VirginiaCommonwealthUniversity  \
0                          0                                    0   
1                          0                                    0   
2                          0                                    0   
3                          0                                    0   
4                          0                                    0   

   Participant_ID_1  Participant_ID_10  Participant_ID_100  \
0                 0                  1                   0   
1                 0                  0                   0   
2                 0                  0                   0   
3                 0                  0                   0   
4                 0                  0                   0   

   Participant_ID_101  Participant_ID_102  Participant_ID_103  \
0                   0                   0                   0   
1                   0                   0                   0   
2                   0                   0                   0   
3                   0                   0         

In [93]:
pred_df_backcount = run(train=df_full, training_epochs=5)

Training Auto Encoders:

Training epoch 0, cost is  0.23801351433575282


Prediction on test data: 

classify
error:  0.012816546040350993


In [97]:
pred_df_backcount['Site_AshlandUniversity'].value_counts(dropna=False)

0    2979
Name: Site_AshlandUniversity, dtype: int64

In [ ]:
df_decode = one_hot_decoding(list(df), encoded_dataframe=pred_df_backcount)
df_decode.head()

In [92]:
pred_df_backcount['Site_MichiganStateUniversity'].value_counts(dropna=False)

0    2979
Name: Site_MichiganStateUniversity, dtype: int64